# MA4620 Final Project: Analysis of Simple Drums

Team Members: Skylar Callis, Ben Lord, Jonathan Oleson, Nick Snell, Luke Wilson

## Finding the Eigenvalues of the Drums

The goal of this project is to analyze the mode shapes and vibration patterns of some simple drums through an analysis of their eigenvalues.

The motion of the drums is modeled with a damped wave equation:

$$u_{tt}+c*u_t=\pm k *\Delta u$$

Where $u$ is a function $u(t,\vec{x})$ defined $\forall \vec{x}$ in the region $\Omega$.

The weak form of the wave equation is obtained through the following derivation:

> Multiply by a test function $\forall v \in H_0^1(\Omega)$: $v*u_{tt}+c*v*u_t=\pm k *\Delta u*v$

> Integrate by $dA$: $\int_{\Omega} v*u_{tt}*dA + c \int_{\Omega} v*u_t*dA = \mp \int_{\Omega} \nabla u*\nabla v*dA$

From the weak form, we can define stiffness and mass matrices, $A$ and $M$, to discretize the equation, just like with any other PDE (partial differential equation):

$$A=∫( ∇(v)⋅∇(u) )dΩ$$

$$M=∫(v*u)*dΩ$$

However, rather than using these to solve the PDE, we will extract the eigenvalues from these matrices by solving the following generalized eigenvalue problem:

$$A*\vec{w_i}=\lambda_i*M*\vec{w_i}$$

The eigenvalues, $\lambda_i$, and the corresponding eigenvectors, $\vec{w_i}$, provide information about the mode shapes of the drums as well as the ratios between modal frequencies. We will focus only on the eigenvalues with the smallest real component since larger eigenvalues are more susceptible to damping and will have a much less noticeable contribution to the physics of the system.

### Setting up the Code

Before analyzing the drums, we need to load a few Julia libraries. Apart from the finite element and meshing libraries, _Gridap_ and _GridapGmsh_, we also use _MatrixMarket_ to allow us to save the matrices and view them in another software. To help with solving the generalized eigenvalue problem, we include _LinearAlgebra_ and _Arpack_ (documentation for _Arpack_ can be found at https://arpack.julialinearalgebra.org/latest/). We also include _Plots_ for visualization. _Interact_ and _WebIO_ are used to visual and interact with plots inside of a jupyter notebook.

In [1]:
using Gridap
using GridapGmsh
using MatrixMarket
using LinearAlgebra
using Arpack
using Plots
using Interact
using WebIO

WebIO._IJuliaInit()

We also made a few functions to process the eigenvalues and eigenvectors for visualization purposes. In Julia, we need to obtain a set of node coordinates excluding the boundary points. This is becuse the Gridap solver doesn't include the Dirichlet boundry points when building it's matricies. Tto properly extract these points, we referred to https://docs.juliahub.com/Gridap/ZIiA2/0.15.2/Geometry/#Gridap.Geometry.get_cell_coordinates-Tuple{Triangulation. 

Once we have solved for the eigenvalues, we need to process them a bit to make sure they are real rather than complex (due to the method of computing the eigenvalues).

We then combine the node coordinates with each corresponding component of the eigenvector as the z-coordinate to give us a set of 3D points with which to make a plot. This enables us to visualize the mode shapes.

In [49]:
function TNoBound(model,A,B,sA,sB,C) # Changes B from vector of vectors to an array of (x,y) points
    # Model : Imported discrete mesh
    # A     : Stiffness matrix
    # B     : Nodes from mesh
    # sA    : The size of our stiffness matrix
    # sB    : Size of B
    # C     : Pre-allocated memory for mapping our new mesh points
    # Bounds: Pre-allocated memory for mapping boundary points
for i = 1: sB[1] 
 A1 = B[i,1] 
  C[i,1] = A1[1]
  C[i,2] = A1[2]
end
 
end
function TEigstuff(A,M,CE,Maxeig,Eigmat,DE) #Finds eig vec/vals and then creates (x,y,z) surface where z is the eigenvector
    # A      : Our stiffness matrix
    # M      : Our mass matrix
    # C      : Node matrix without the boundaries
    # CE     : Pre-allocated memory for mapping eigenvectors
    # Maxeig : maximum number of eig values we wish to solve for
    # DE     : Stores all of our Eigen matrices
eigval,eigvec=eigs(A,M; nev=Maxeig,which=:SR) # Calcs eigenvalues and vectors of our GEP
eigval=real(eigval) # Chops the miniscule imaginary parts
    Eigmat[:,1] = eigval
for j = 1:Maxeig
    CE[1:sB[1]-sA[1],3] = zeros(sB[1] - sA[1])
        CE[(sB[1]-sA[1])+1:end,3] = eigvec[:,j]
    DE[j] = CE[:,:]
end
end


TEigstuff (generic function with 1 method)

### The Circle Drum

First, we solve for the eigenvalues on the circular drum. We begin by loading the mesh, setting up the solver, and building the weak form depicted above. We then extract the matrices and solve the generalized eigenvalue problem.

In [50]:
#Loading in the Drum Mesh
model = GmshDiscreteModel("circledrum.msh");

#Setting Up the Solver
order = 1
reffe = ReferenceFE(lagrangian,Float64,order)
V = TestFESpace(model,reffe,dirichlet_tags="rim")
U = TrialFESpace(V,0) #dirichlet condition = 0 on the rim
degree = 2
Ω = Triangulation(model)
dΩ = Measure(Ω,degree)

#Building the Weak Form
a(u,v) = ∫( ∇(v)⋅∇(u) )dΩ 
l(v) = 0
m(u,v) = ∫(v*u)*dΩ 

#Getting the Stiffness Matrix (A)
op = AffineFEOperator(a,l,U,V) 
A_circle = get_matrix(op)

#Getting the Mass Matrix (M)                      
mop = AffineFEOperator(m,l,U,V)  
M_circle = get_matrix(mop) 

Info    : Reading 'circledrum.msh'...
Info    : 10 entities
Info    : 1320 nodes
Info    : 2642 elements
Info    : Done reading 'circledrum.msh'


1204×1204 SparseArrays.SparseMatrixCSC{Float64, Int64} with 8186 stored entries:
⢑⢔⡂⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⣼⣇⠐⠀⠄⠘⠀⠈⠱⠁⠑⠤⠈⡄⢰⣿⣿⣿⣿
⠈⠈⠻⣦⣀⠀⠀⠀⠀⠀⡄⠠⢠⠀⡀⠀⠀⠀⠠⠀⠀⠀⠸⠃⠷⠀⠀⠀⢀⢐⡀⢀⡔⠀⢴⠋⠈⠈⠀⠀
⠀⠀⠀⠘⢻⣶⣆⢁⠓⡠⡆⠀⠘⠀⠀⠀⠘⢈⠀⠀⠀⠀⠀⠀⠀⡂⣌⢸⡌⡇⢃⢜⠻⣀⠺⠇⠀⠀⠀⠀
⠀⠀⠀⠀⠌⢙⢿⣷⣄⣁⡅⡀⠆⢭⠀⠀⠀⠈⠁⠀⠀⠀⠀⢠⠀⠒⡆⠈⣧⣰⣿⣦⣷⡃⠠⠇⠀⠀⠀⠀
⠀⠀⠀⠀⠙⡠⠄⢹⡿⣯⣻⣷⢄⠵⠀⡄⢈⠄⠀⠠⠀⠀⠀⠊⠀⡰⠭⢇⡅⣕⠿⣞⠚⡋⠓⡀⠀⠀⠀⠀
⠀⠀⠀⡉⠈⠉⠁⠩⢿⣾⣿⣿⣷⠄⣦⣇⠂⠠⢁⠀⠀⠀⠀⣉⣭⣺⠲⡩⡯⡟⡷⡩⡗⡛⣍⠁⠀⠀⠀⠀
⠀⠀⠀⠒⠒⠀⡌⣅⢄⡕⠙⠟⠛⣤⡼⣛⡷⢸⠉⠈⡏⠀⠀⠀⠣⠛⠘⠓⣿⠣⢯⣽⣟⢆⠑⠠⠀⠀⠀⠀
⠀⠀⠀⠈⠀⠀⠀⠀⠀⠤⠬⢿⣶⢫⣟⢝⡿⡿⢺⣾⣕⡀⠐⡖⡺⡼⢸⠢⠟⣺⢏⣄⡧⣚⢤⣅⠀⠀⠀⠀
⠀⠀⠀⠀⡒⢀⡀⠀⠂⠔⠈⡀⣙⣋⣿⡯⡛⢌⡨⢗⢫⠩⠁⠅⣩⠛⢾⢓⣿⢊⣁⣆⣥⢬⢌⠌⡀⠀⠀⠀
⠀⠀⠀⠂⠀⠀⠁⠀⠀⡀⠁⠐⡃⠀⣺⣶⢦⢎⡱⣮⢱⣯⢎⡀⣓⣤⣎⣀⡘⡷⢝⡚⡚⡟⡛⢦⠀⣤⡀⠂
⣀⣤⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠋⠉⠑⠹⡏⡒⡵⣶⠱⣦⡶⠇⠧⣘⢦⡁⡙⠈⢹⠳⣛⡻⡏⣳⣦⣲⢶⣤
⢉⠙⠶⠂⠀⠀⠀⣀⡠⠀⡄⢠⠀⠀⢰⠤⠅⠄⠊⠱⠼⠏⠻⣦⣮⠈⠀⠀⠉⠌⠠⣠⠁⠶⣳⣞⠋⡙⢉⠃
⠀⠄⠙⠃⠠⠠⢠⠀⢀⡠⣣⣻⣭⠂⣚⡮⣧⠚⠙⣼⣉⢣⡊⠛⢛⣴⣄⡤⠸⠃⠀⡘⠆⡈⢛⠏⠀⢌⢢⠁
⠒⠀⠀⠀⣂⣙⡈⠉⠧⢇⡜⡢⢶⠀⠲⡒⢾⢓⠊⢹⠌⠳⠀⠀⠀⡽⢻⣶⡉⡂⢐⠠⡡⠑⠁⡻⠓⠓⠆⠒
⢆⡀⢀⢐⠦⠭⢉⣻⢅⢭⣯⠯⠿⡛⣻⣡⡻⢛⢶⡬⡓⠈⡃⠄⠶⠂⠣⠨⣛⢜⢘⡫⣫⣯⠶⣄⠀⡦⣰⠀
⢅⠀⠀⢈⣉⢔⠻⣿⣻⢧⡝⡫⣏⣷⠋⢵⠡⢼⣳⠱⢷⡒⠀⣢⣀⠠⠐⡐⡶⡰⡻⣮⣻⣙⢳⢆⢀⠡⠀⡁
⡀⠃⠐⠉⠛⢢⠽⠻⡾⠠⣽⠩⠻⢝⣩⢫⡁⣟⣾⠬⣿⡸⢡⡄⡈⠡⢅⠊⡯⣾⣟⢺⢿⣷⣯⡯⡁⠐⣍⠉
⢀⣉⡴⠓⠾⠆⠤⠆⠙⠠⠇⠙⠑⡀⠄⢷⡂⠕⠻⣌⢯⣩⣹⢾⡿⠔⣥⡠⠘⢧⠹⢖⡯⡿⡻⢎⣈⣡⣨⡡
⣿⣿⡂⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠈⠀⣤⢨⣻⣏⠠⡀⢄⢽⠀⠠⡤⠄⡐⢁⠈⠆⣸⣿⣿⣿⣿
⣿⣿⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠠⠈⠘⣷⠧⠐⠌⠒⢨⠁⠐⠚⠄⠠⡇⠙⠆⡺⣿⣿⣟⣽

The mass matrix is plotted above for demonstration purposes. Note the sparseness of the matrix.

To make sure the visualization will work correctly, we do a bit more checking on the circle than the other shapes.

In [51]:
B =Gridap.ReferenceFEs.get_node_coordinates(model) # Finds our node coordinates
sB = size(B) # Number of nodes
sA = size(A_circle) # number of equations
Maxeig = 5 # Max eigenval/vecs we want to solve for

#Pre-allocate
CE = Array{Float64}(undef,sB[1],3)
C = Array{Float64}(undef,sB[1],2)
DE = Matrix{Matrix{Float64}}(undef,Maxeig,1)
Eigmat = Matrix{Float64}(undef,Maxeig,1)

TNoBound(model,A_circle,B,sA,sB,C)
CE[:,1:2] = C #Initializing CE
TEigstuff(A_circle,M_circle,CE,Maxeig,Eigmat,DE);

In [52]:
#Manipulating the plot that doesn't work for some of us
@manipulate for j = 1:Maxeig
    surface(DE[j][:,1],DE[j][:,2],DE[j][:,3],
    size = [100,100,100],thickness_scaling = .01,camera =(10,50),colorbar = false)
    end

Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Scope(Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :label), Any["j"], Dict{Symbol, Any}(:className => "interact ", :style => Dict{Any, Any}(:padding => "5px 10px 0px 10px")))], Dict{Symbol, Any}(:className => "interact-flex-row-left")), Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :input), Any[], Dict{Symbol, Any}(:max => 5, :min => 1, :attributes => Dict{Any, Any}(:type => "range", Symbol("data-bind") => "numericValue: index, valueUpdate: 'input', event: {change: function (){this.changes(this.changes()+1)}}", "orient" => "horizontal"), :step => 1, :className => "slider slider is-fullwidth", :style => Dict{Any, Any}()))], Dict{Symbol, Any}(:className => "interact-flex-row-center")), Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :p), Any[], Dict{Symbol, Any}(:attributes => Dict("data-bind" => "text: formatted_val")))], Dict{Symbol, Any}(:className => "interact-flex-row-right"))], Dict{Symbol, Any}(:className => "interact-flex-row interact-widget")), Dict{String, Tuple{Observables.AbstractObservable, Union{Nothing, Bool}}}("changes" => (Observable{Int64} with 1 listeners. Value:
0, nothing), "index" => (Observable{Int64} with 2 listeners. Value:
3, nothing)), Set{String}(), nothing, Asset[Asset("js", "knockout", "C:\\Users\\nicks\\.julia\\packages\\Knockout\\3gjS1\\src\\..\\assets\\knockout.js"), Asset("js", "knockout_punches", "C:\\Users\\nicks\\.julia\\packages\\Knockout\\3gjS1\\src\\..\\assets\\knockout_punches.js"), Asset("js", nothing, "C:\\Users\\nicks\\.julia\\packages\\InteractBase\\o1I6G\\src\\..\\assets\\all.js"), Asset("css", nothing, "C:\\Users\\nicks\\.julia\\packages\\InteractBase\\o1I6G\\src\\..\\assets\\style.css"), Asset("css", nothing, "C:\\Users\\nicks\\.julia\\packages\\Interact\\pVyN2\\src\\..\\assets\\bulma_confined.min.css")], Dict{Any, Any}("changes" => Any[WebIO.JSString("(function (val){return (val!=this.model[\"changes\"]()) ? (this.valueFromJulia[\"changes\"]=true, this.model[\"changes\"](val)) : undefined})")], "index" => Any[WebIO.JSString("(function (val){return (val!=this.model[\"index\"]()) ? (this.valueFromJulia[\"index\"]=true, this.model[\"index\"](val)) : undefined})")]), WebIO.ConnectionPool(Channel{Any}(32), Set{AbstractConnection}(), Condition(Base.InvasiveLinkedList{Task}(Task (runnable) @0x0000000019650010, Task (runnable) @0x0000000019650010), Base.AlwaysLockedST(1))), WebIO.JSString[WebIO.JSString("function () {\n    var handler = (function (ko, koPunches) {\n    ko.punches.enableAll();\n    ko.bindingHandlers.numericValue = {\n        init: function(element, valueAccessor, allBindings, data, context) {\n            var stringified = ko.observable(ko.unwrap(valueAccessor()));\n            stringified.subscribe(function(value) {\n                var val = parseFloat(value);\n                if (!isNaN(val)) {\n                    valueAccessor()(val);\n                }\n            });\n            valueAccessor().subscribe(function(value) {\n                var str = JSON.stringify(value);\n                if ((str == \"0\") && ([\"-0\", \"-0.\"].indexOf(stringified()) >= 0))\n                     return;\n                 if ([\"null\", \"\"].indexOf(str) >= 0)\n                     return;\n                stringified(str);\n            });\n            ko.applyBindingsToNode(\n                element,\n                {\n                    value: stringified,\n                    valueUpdate: allBindings.get('valueUpdate'),\n                },\n                context,\n            );\n        }\n    };\n    var json_data = {\"formatted_vals\":[\"1\",\"2\",\"3\",\"4\",\"5\"],\"changes\":WebIO.getval({\"name\":\"changes\",\"scope\":\"10774101813942965223\",\"id\":\"13552251183140609314\",\"type\":\"observable\"}),\"index\":WebIO.getval({\"name\":\"index\",\"s

The eigenvalues correspond to modal frequencies of the system. For the circle drum, the first mode is simply raised/lowered in the center and displays circular symmetry. The next two are symmetric across either the x- or y- axis and have one half raised and the other half lowered. The final two modes display axial symmetry again, this time with four distinct regions alternating between raised and lowered. Higher eigenvalues will follow similar patterns, with some displaying circular symmetry and many others displaying axial symmetry. You can also see this symmetry in how the eigen values of the repeate

The individual eigenvalues are not very meaningful, but the ratios between them can tell you the relative frequencies at which the drum would vibrate when struck (assuming the equation sufficiently describes the physical behavior of the drum, which is probably not the case due to things like air loading and the interaction between the drum membrane and the outer rim).

### Square Drum

We follow the same process for the square drum.

In [66]:
#Loading in the Drum Mesh
model = GmshDiscreteModel("squaredrum.msh")

#Setting Up the Solver
order = 1
reffe = ReferenceFE(lagrangian,Float64,order)
V = TestFESpace(model,reffe,dirichlet_tags="rim")
U = TrialFESpace(V,0) #dirichlet condition = 0 on the rim
degree = 2
Ω = Triangulation(model)
dΩ = Measure(Ω,degree)

#Building the Weak Form
a(u,v) = ∫( ∇(v)⋅∇(u) )dΩ 
l(v) = 0 
m(u,v) = ∫(v*u)*dΩ 

#Getting the Stiffness Matrix (A)
op = AffineFEOperator(a,l,U,V) 
A_square = get_matrix(op)

#Getting the Mass Matrix (M)                      
mop = AffineFEOperator(m,l,U,V)  
M_square = get_matrix(mop) 



B =Gridap.ReferenceFEs.get_node_coordinates(model) # Finds our node coordinates
sB = size(B) # Number of nodes
sA = size(A_square) # number of equations
Maxeig = 20 # Max eigenval/vecs we want to solve for

#Pre-allocate
CE = Array{Float64}(undef,sB[1],3)
C = Array{Float64}(undef,sB[1],2)
DE = Matrix{Matrix{Float64}}(undef,Maxeig,1)
Eigmat = Matrix{Float64}(undef,Maxeig,1)

TNoBound(model,A_square,B,sA,sB,C)
CE[:,1:2] = C #Initializing CE
TEigstuff(A_square,M_square,CE,Maxeig,Eigmat,DE);

@manipulate for j = 1:Maxeig
    surface(DE[j][:,1],DE[j][:,2],DE[j][:,3],
    size = [100,100,100],thickness_scaling = .01,camera =(30,40),colorbar = false)
    end

Info    : Reading 'squaredrum.msh'...
Info    : 21 entities
Info    : 436 nodes
Info    : 870 elements
Info    : Done reading 'squaredrum.msh'


Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Scope(Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :label), Any["j"], Dict{Symbol, Any}(:className => "interact ", :style => Dict{Any, Any}(:padding => "5px 10px 0px 10px")))], Dict{Symbol, Any}(:className => "interact-flex-row-left")), Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :input), Any[], Dict{Symbol, Any}(:max => 20, :min => 1, :attributes => Dict{Any, Any}(:type => "range", Symbol("data-bind") => "numericValue: index, valueUpdate: 'input', event: {change: function (){this.changes(this.changes()+1)}}", "orient" => "horizontal"), :step => 1, :className => "slider slider is-fullwidth", :style => Dict{Any, Any}()))], Dict{Symbol, Any}(:className => "interact-flex-row-center")), Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :p), Any[], Dict{Symbol, Any}(:attributes => Dict("data-bind" => "text: formatted_val")))], Dict{Symbol, Any}(:className => "interact-flex-row-right"))], Dict{Symbol, Any}(:className => "interact-flex-row interact-widget")), Dict{String, Tuple{Observables.AbstractObservable, Union{Nothing, Bool}}}("changes" => (Observable{Int64} with 1 listeners. Value:
0, nothing), "index" => (Observable{Int64} with 2 listeners. Value:
10, nothing)), Set{String}(), nothing, Asset[Asset("js", "knockout", "C:\\Users\\nicks\\.julia\\packages\\Knockout\\3gjS1\\src\\..\\assets\\knockout.js"), Asset("js", "knockout_punches", "C:\\Users\\nicks\\.julia\\packages\\Knockout\\3gjS1\\src\\..\\assets\\knockout_punches.js"), Asset("js", nothing, "C:\\Users\\nicks\\.julia\\packages\\InteractBase\\o1I6G\\src\\..\\assets\\all.js"), Asset("css", nothing, "C:\\Users\\nicks\\.julia\\packages\\InteractBase\\o1I6G\\src\\..\\assets\\style.css"), Asset("css", nothing, "C:\\Users\\nicks\\.julia\\packages\\Interact\\pVyN2\\src\\..\\assets\\bulma_confined.min.css")], Dict{Any, Any}("changes" => Any[WebIO.JSString("(function (val){return (val!=this.model[\"changes\"]()) ? (this.valueFromJulia[\"changes\"]=true, this.model[\"changes\"](val)) : undefined})")], "index" => Any[WebIO.JSString("(function (val){return (val!=this.model[\"index\"]()) ? (this.valueFromJulia[\"index\"]=true, this.model[\"index\"](val)) : undefined})")]), WebIO.ConnectionPool(Channel{Any}(32), Set{AbstractConnection}(), Condition(Base.InvasiveLinkedList{Task}(Task (runnable) @0x0000000019740b00, Task (runnable) @0x0000000019740b00), Base.AlwaysLockedST(1))), WebIO.JSString[WebIO.JSString("function () {\n    var handler = (function (ko, koPunches) {\n    ko.punches.enableAll();\n    ko.bindingHandlers.numericValue = {\n        init: function(element, valueAccessor, allBindings, data, context) {\n            var stringified = ko.observable(ko.unwrap(valueAccessor()));\n            stringified.subscribe(function(value) {\n                var val = parseFloat(value);\n                if (!isNaN(val)) {\n                    valueAccessor()(val);\n                }\n            });\n            valueAccessor().subscribe(function(value) {\n                var str = JSON.stringify(value);\n                if ((str == \"0\") && ([\"-0\", \"-0.\"].indexOf(stringified()) >= 0))\n                     return;\n                 if ([\"null\", \"\"].indexOf(str) >= 0)\n                     return;\n                stringified(str);\n            });\n            ko.applyBindingsToNode(\n                element,\n                {\n                    value: stringified,\n                    valueUpdate: allBindings.get('valueUpdate'),\n                },\n                context,\n            );\n        }\n    };\n    var json_data = {\"formatted_vals\":[\"1\",\"2\",\"3\",\"4\",\"5\",\"6\",\"7\",\"8\",\"9\",\"10\",\"11\",\"12\",\"13\",\"14\",\"15\",\"16\",\"17\",\"18\",\"19\",\"20\"],\"changes\":WebIO.getval({\"name\":\"changes\",\"scope\":\"11336730465417833413\",\

The plots for the square drum show similar mode shapes to the circle. The first mode shape is one large deformation centered, while 2 & 3 are a symmetric pair of half raised and half lowered. 

### Rectangle Drum

We repeat this for the rectangle drum.

In [55]:
#Loading in the Drum Mesh
model = GmshDiscreteModel("rectangledrum.msh")

#Setting Up the Solver
order = 1
reffe = ReferenceFE(lagrangian,Float64,order)
V = TestFESpace(model,reffe,dirichlet_tags="rim")
U = TrialFESpace(V,0) #dirichlet condition = 0 on the rim
degree = 2
Ω = Triangulation(model)
dΩ = Measure(Ω,degree)

#Building the Weak Form
a(u,v) = ∫( ∇(v)⋅∇(u) )dΩ 
l(v) = 0 
m(u,v) = ∫(v*u)*dΩ 

#Getting the Stiffness Matrix (A)
op = AffineFEOperator(a,l,U,V) 
A_rect = get_matrix(op)

#Getting the Mass Matrix (M)                      
mop = AffineFEOperator(m,l,U,V)  
M_rect = get_matrix(mop) 


B =Gridap.ReferenceFEs.get_node_coordinates(model) # Finds our node coordinates
sB = size(B) # Number of nodes
sA = size(A_rect) # number of equations
Maxeig = 5 # Max eigenval/vecs we want to solve for

#Pre-allocate
CE = Array{Float64}(undef,sB[1],3)
C = Array{Float64}(undef,sB[1],2)
DE = Matrix{Matrix{Float64}}(undef,Maxeig,1)
Eigmat = Matrix{Float64}(undef,Maxeig,1)

TNoBound(model,A_rect,B,sA,sB,C)
CE[:,1:2] = C #Initializing CE
eigval=TEigstuff(A_rect,M_rect,CE,Maxeig,Eigmat,DE);

@manipulate for j = 1:Maxeig
    surface(DE[j][:,1],DE[j][:,2],DE[j][:,3],
    size = [100,100,100],thickness_scaling = .01,camera =(20,50),colorbar = false)
    end

Info    : Reading 'rectangledrum.msh'...
Info    : 25 entities
Info    : 298 nodes
Info    : 602 elements
Info    : Done reading 'rectangledrum.msh'


Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Scope(Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :label), Any["j"], Dict{Symbol, Any}(:className => "interact ", :style => Dict{Any, Any}(:padding => "5px 10px 0px 10px")))], Dict{Symbol, Any}(:className => "interact-flex-row-left")), Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :input), Any[], Dict{Symbol, Any}(:max => 5, :min => 1, :attributes => Dict{Any, Any}(:type => "range", Symbol("data-bind") => "numericValue: index, valueUpdate: 'input', event: {change: function (){this.changes(this.changes()+1)}}", "orient" => "horizontal"), :step => 1, :className => "slider slider is-fullwidth", :style => Dict{Any, Any}()))], Dict{Symbol, Any}(:className => "interact-flex-row-center")), Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :p), Any[], Dict{Symbol, Any}(:attributes => Dict("data-bind" => "text: formatted_val")))], Dict{Symbol, Any}(:className => "interact-flex-row-right"))], Dict{Symbol, Any}(:className => "interact-flex-row interact-widget")), Dict{String, Tuple{Observables.AbstractObservable, Union{Nothing, Bool}}}("changes" => (Observable{Int64} with 1 listeners. Value:
0, nothing), "index" => (Observable{Int64} with 2 listeners. Value:
3, nothing)), Set{String}(), nothing, Asset[Asset("js", "knockout", "C:\\Users\\nicks\\.julia\\packages\\Knockout\\3gjS1\\src\\..\\assets\\knockout.js"), Asset("js", "knockout_punches", "C:\\Users\\nicks\\.julia\\packages\\Knockout\\3gjS1\\src\\..\\assets\\knockout_punches.js"), Asset("js", nothing, "C:\\Users\\nicks\\.julia\\packages\\InteractBase\\o1I6G\\src\\..\\assets\\all.js"), Asset("css", nothing, "C:\\Users\\nicks\\.julia\\packages\\InteractBase\\o1I6G\\src\\..\\assets\\style.css"), Asset("css", nothing, "C:\\Users\\nicks\\.julia\\packages\\Interact\\pVyN2\\src\\..\\assets\\bulma_confined.min.css")], Dict{Any, Any}("changes" => Any[WebIO.JSString("(function (val){return (val!=this.model[\"changes\"]()) ? (this.valueFromJulia[\"changes\"]=true, this.model[\"changes\"](val)) : undefined})")], "index" => Any[WebIO.JSString("(function (val){return (val!=this.model[\"index\"]()) ? (this.valueFromJulia[\"index\"]=true, this.model[\"index\"](val)) : undefined})")]), WebIO.ConnectionPool(Channel{Any}(32), Set{AbstractConnection}(), Condition(Base.InvasiveLinkedList{Task}(Task (runnable) @0x000000001bfa52d0, Task (runnable) @0x000000001bfa52d0), Base.AlwaysLockedST(1))), WebIO.JSString[WebIO.JSString("function () {\n    var handler = (function (ko, koPunches) {\n    ko.punches.enableAll();\n    ko.bindingHandlers.numericValue = {\n        init: function(element, valueAccessor, allBindings, data, context) {\n            var stringified = ko.observable(ko.unwrap(valueAccessor()));\n            stringified.subscribe(function(value) {\n                var val = parseFloat(value);\n                if (!isNaN(val)) {\n                    valueAccessor()(val);\n                }\n            });\n            valueAccessor().subscribe(function(value) {\n                var str = JSON.stringify(value);\n                if ((str == \"0\") && ([\"-0\", \"-0.\"].indexOf(stringified()) >= 0))\n                     return;\n                 if ([\"null\", \"\"].indexOf(str) >= 0)\n                     return;\n                stringified(str);\n            });\n            ko.applyBindingsToNode(\n                element,\n                {\n                    value: stringified,\n                    valueUpdate: allBindings.get('valueUpdate'),\n                },\n                context,\n            );\n        }\n    };\n    var json_data = {\"formatted_vals\":[\"1\",\"2\",\"3\",\"4\",\"5\"],\"changes\":WebIO.getval({\"name\":\"changes\",\"scope\":\"6991878921636436087\",\"id\":\"17970682714621241096\",\"type\":\"observable\"}),\"index\":WebIO.getval({\"name\":\"index\",\"sc

The rectangle drum has similar 1st, 2nd, and 3rd mode shapes to the square. A difference becomes apparent in the fourth mode, which is a series of three alternating raised and lowered sections running in the long direction. This likely is caused by the difference in the length:width ratio in the rectangle vs. the square.

### Triangle Drum

We also do this for a triangle drum.

In [56]:
#Loading in the Drum Mesh
model = GmshDiscreteModel("Triangledrum.msh")

#Setting Up the Solver
order = 1
reffe = ReferenceFE(lagrangian,Float64,order)
V = TestFESpace(model,reffe,dirichlet_tags="rim")
U = TrialFESpace(V,0) #dirichlet condition = 0 on the rim
degree = 2
Ω = Triangulation(model)
dΩ = Measure(Ω,degree)

#Building the Weak Form
a(u,v) = ∫( ∇(v)⋅∇(u) )dΩ 
l(v) = 0 
m(u,v) = ∫(v*u)*dΩ 

#Getting the Stiffness Matrix (A)
op = AffineFEOperator(a,l,U,V) 
A_tri = get_matrix(op)

#Getting the Mass Matrix (M)                      
mop = AffineFEOperator(m,l,U,V)  
M_tri = get_matrix(mop) 

B =Gridap.ReferenceFEs.get_node_coordinates(model) # Finds our node coordinates
sB = size(B) # Number of nodes
sA = size(A_tri) # number of equations
Maxeig = 5 # Max eigenval/vecs we want to solve for

#Pre-allocate
CE = Array{Float64}(undef,sB[1],3)
C = Array{Float64}(undef,sB[1],2)
DE = Matrix{Matrix{Float64}}(undef,Maxeig,1)
Eigmat = Matrix{Float64}(undef,Maxeig,1)

TNoBound(model,A_tri,B,sA,sB,C)
CE[:,1:2] = C #Initializing CE
TEigstuff(A_tri,M_tri,CE,Maxeig,Eigmat,DE);

@manipulate for j = 1:Maxeig

    surface(DE[j][:,1],DE[j][:,2],DE[j][:,3],
    size = [100,100,100],thickness_scaling = .01,camera =(20,50),colorbar = false)
end

Info    : Reading 'Triangledrum.msh'...
Info    : 19 entities
Info    : 177 nodes
Info    : 355 elements
Info    : Done reading 'Triangledrum.msh'


Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Scope(Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :label), Any["j"], Dict{Symbol, Any}(:className => "interact ", :style => Dict{Any, Any}(:padding => "5px 10px 0px 10px")))], Dict{Symbol, Any}(:className => "interact-flex-row-left")), Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :input), Any[], Dict{Symbol, Any}(:max => 5, :min => 1, :attributes => Dict{Any, Any}(:type => "range", Symbol("data-bind") => "numericValue: index, valueUpdate: 'input', event: {change: function (){this.changes(this.changes()+1)}}", "orient" => "horizontal"), :step => 1, :className => "slider slider is-fullwidth", :style => Dict{Any, Any}()))], Dict{Symbol, Any}(:className => "interact-flex-row-center")), Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :p), Any[], Dict{Symbol, Any}(:attributes => Dict("data-bind" => "text: formatted_val")))], Dict{Symbol, Any}(:className => "interact-flex-row-right"))], Dict{Symbol, Any}(:className => "interact-flex-row interact-widget")), Dict{String, Tuple{Observables.AbstractObservable, Union{Nothing, Bool}}}("changes" => (Observable{Int64} with 1 listeners. Value:
0, nothing), "index" => (Observable{Int64} with 2 listeners. Value:
3, nothing)), Set{String}(), nothing, Asset[Asset("js", "knockout", "C:\\Users\\nicks\\.julia\\packages\\Knockout\\3gjS1\\src\\..\\assets\\knockout.js"), Asset("js", "knockout_punches", "C:\\Users\\nicks\\.julia\\packages\\Knockout\\3gjS1\\src\\..\\assets\\knockout_punches.js"), Asset("js", nothing, "C:\\Users\\nicks\\.julia\\packages\\InteractBase\\o1I6G\\src\\..\\assets\\all.js"), Asset("css", nothing, "C:\\Users\\nicks\\.julia\\packages\\InteractBase\\o1I6G\\src\\..\\assets\\style.css"), Asset("css", nothing, "C:\\Users\\nicks\\.julia\\packages\\Interact\\pVyN2\\src\\..\\assets\\bulma_confined.min.css")], Dict{Any, Any}("changes" => Any[WebIO.JSString("(function (val){return (val!=this.model[\"changes\"]()) ? (this.valueFromJulia[\"changes\"]=true, this.model[\"changes\"](val)) : undefined})")], "index" => Any[WebIO.JSString("(function (val){return (val!=this.model[\"index\"]()) ? (this.valueFromJulia[\"index\"]=true, this.model[\"index\"](val)) : undefined})")]), WebIO.ConnectionPool(Channel{Any}(32), Set{AbstractConnection}(), Condition(Base.InvasiveLinkedList{Task}(Task (runnable) @0x000000001bfa6270, Task (runnable) @0x000000001bfa6270), Base.AlwaysLockedST(1))), WebIO.JSString[WebIO.JSString("function () {\n    var handler = (function (ko, koPunches) {\n    ko.punches.enableAll();\n    ko.bindingHandlers.numericValue = {\n        init: function(element, valueAccessor, allBindings, data, context) {\n            var stringified = ko.observable(ko.unwrap(valueAccessor()));\n            stringified.subscribe(function(value) {\n                var val = parseFloat(value);\n                if (!isNaN(val)) {\n                    valueAccessor()(val);\n                }\n            });\n            valueAccessor().subscribe(function(value) {\n                var str = JSON.stringify(value);\n                if ((str == \"0\") && ([\"-0\", \"-0.\"].indexOf(stringified()) >= 0))\n                     return;\n                 if ([\"null\", \"\"].indexOf(str) >= 0)\n                     return;\n                stringified(str);\n            });\n            ko.applyBindingsToNode(\n                element,\n                {\n                    value: stringified,\n                    valueUpdate: allBindings.get('valueUpdate'),\n                },\n                context,\n            );\n        }\n    };\n    var json_data = {\"formatted_vals\":[\"1\",\"2\",\"3\",\"4\",\"5\"],\"changes\":WebIO.getval({\"name\":\"changes\",\"scope\":\"6587617751083862398\",\"id\":\"4111478528552006477\",\"type\":\"observable\"}),\"index\":WebIO.getval({\"name\":\"index\",\"sco

The mode shapes for the triangle will follow a similar pattern to the others, but with triangular symmetry. Note that there will only be two different modes displayed for the same eigenvalue rather than three. The third can be obtained as a linear combination of the other two, so it does not appear as it's own mode shape.

### Semicircle Drum

Lastly, we find the eigenvalues for a semicircle drum.

In [60]:
#Loading in the Drum Mesh
model = GmshDiscreteModel("Semicircledrum.msh")

#Setting Up the Solver
order = 1
reffe = ReferenceFE(lagrangian,Float64,order)
V = TestFESpace(model,reffe,dirichlet_tags="rim")
U = TrialFESpace(V,0) #dirichlet condition = 0 on the rim
degree = 2
Ω = Triangulation(model)
dΩ = Measure(Ω,degree)

#Building the Weak Form
a(u,v) = ∫( ∇(v)⋅∇(u) )dΩ 
l(v) = 0 
m(u,v) = ∫(v*u)*dΩ 

#Getting the Stiffness Matrix (A)
op = AffineFEOperator(a,l,U,V) 
A_semi = get_matrix(op)

#Getting the Mass Matrix (M)                      
mop = AffineFEOperator(m,l,U,V)  
M_semi = get_matrix(mop) 

B =Gridap.ReferenceFEs.get_node_coordinates(model) # Finds our node coordinates
sB = size(B) # Number of nodes
sA = size(A_semi) # number of equations
Maxeig = 5 # Max eigenval/vecs we want to solve for

#Pre-allocate
CE = Array{Float64}(undef,sB[1],3)
C = Array{Float64}(undef,sB[1],2)
DE = Matrix{Matrix{Float64}}(undef,Maxeig,1)
Eigmat = Matrix{Float64}(undef,Maxeig,1)

TNoBound(model,A_semi,B,sA,sB,C)
CE[:,1:2] = C #Initializing CE
TEigstuff(A_semi,M_semi,CE,Maxeig,Eigmat,DE);

@manipulate for j = 1:Maxeig
    surface(DE[j][:,1],DE[j][:,2],DE[j][:,3],
    size = [100,100,100],thickness_scaling = .01,camera =(30,40),colorbar = false)
    end

Info    : Reading 'Semicircledrum.msh'...
Info    : 18 entities
Info    : 148 nodes
Info    : 298 elements
Info    : Done reading 'Semicircledrum.msh'


Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Scope(Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :label), Any["j"], Dict{Symbol, Any}(:className => "interact ", :style => Dict{Any, Any}(:padding => "5px 10px 0px 10px")))], Dict{Symbol, Any}(:className => "interact-flex-row-left")), Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :input), Any[], Dict{Symbol, Any}(:max => 5, :min => 1, :attributes => Dict{Any, Any}(:type => "range", Symbol("data-bind") => "numericValue: index, valueUpdate: 'input', event: {change: function (){this.changes(this.changes()+1)}}", "orient" => "horizontal"), :step => 1, :className => "slider slider is-fullwidth", :style => Dict{Any, Any}()))], Dict{Symbol, Any}(:className => "interact-flex-row-center")), Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :p), Any[], Dict{Symbol, Any}(:attributes => Dict("data-bind" => "text: formatted_val")))], Dict{Symbol, Any}(:className => "interact-flex-row-right"))], Dict{Symbol, Any}(:className => "interact-flex-row interact-widget")), Dict{String, Tuple{Observables.AbstractObservable, Union{Nothing, Bool}}}("changes" => (Observable{Int64} with 1 listeners. Value:
0, nothing), "index" => (Observable{Int64} with 2 listeners. Value:
3, nothing)), Set{String}(), nothing, Asset[Asset("js", "knockout", "C:\\Users\\nicks\\.julia\\packages\\Knockout\\3gjS1\\src\\..\\assets\\knockout.js"), Asset("js", "knockout_punches", "C:\\Users\\nicks\\.julia\\packages\\Knockout\\3gjS1\\src\\..\\assets\\knockout_punches.js"), Asset("js", nothing, "C:\\Users\\nicks\\.julia\\packages\\InteractBase\\o1I6G\\src\\..\\assets\\all.js"), Asset("css", nothing, "C:\\Users\\nicks\\.julia\\packages\\InteractBase\\o1I6G\\src\\..\\assets\\style.css"), Asset("css", nothing, "C:\\Users\\nicks\\.julia\\packages\\Interact\\pVyN2\\src\\..\\assets\\bulma_confined.min.css")], Dict{Any, Any}("changes" => Any[WebIO.JSString("(function (val){return (val!=this.model[\"changes\"]()) ? (this.valueFromJulia[\"changes\"]=true, this.model[\"changes\"](val)) : undefined})")], "index" => Any[WebIO.JSString("(function (val){return (val!=this.model[\"index\"]()) ? (this.valueFromJulia[\"index\"]=true, this.model[\"index\"](val)) : undefined})")]), WebIO.ConnectionPool(Channel{Any}(32), Set{AbstractConnection}(), Condition(Base.InvasiveLinkedList{Task}(Task (runnable) @0x000000001b9df3a0, Task (runnable) @0x000000001b9df3a0), Base.AlwaysLockedST(1))), WebIO.JSString[WebIO.JSString("function () {\n    var handler = (function (ko, koPunches) {\n    ko.punches.enableAll();\n    ko.bindingHandlers.numericValue = {\n        init: function(element, valueAccessor, allBindings, data, context) {\n            var stringified = ko.observable(ko.unwrap(valueAccessor()));\n            stringified.subscribe(function(value) {\n                var val = parseFloat(value);\n                if (!isNaN(val)) {\n                    valueAccessor()(val);\n                }\n            });\n            valueAccessor().subscribe(function(value) {\n                var str = JSON.stringify(value);\n                if ((str == \"0\") && ([\"-0\", \"-0.\"].indexOf(stringified()) >= 0))\n                     return;\n                 if ([\"null\", \"\"].indexOf(str) >= 0)\n                     return;\n                stringified(str);\n            });\n            ko.applyBindingsToNode(\n                element,\n                {\n                    value: stringified,\n                    valueUpdate: allBindings.get('valueUpdate'),\n                },\n                context,\n            );\n        }\n    };\n    var json_data = {\"formatted_vals\":[\"1\",\"2\",\"3\",\"4\",\"5\"],\"changes\":WebIO.getval({\"name\":\"changes\",\"scope\":\"13489544237361333841\",\"id\":\"14015662475585118629\",\"type\":\"observable\"}),\"index\":WebIO.getval({\"name\":\"index\",\"s

The mode shapes for the semicircle follow a similar pattern of humps as all the other shapes. However, since the semicircle isn't a very symmetric shape, none of the mode shapes exhibit symmetry. This is reflected that all the eigenvalues are unique from eachother.